In [1]:
import math
import pandas as pd
import tensorflow as tf
import matplotlib.pyplot as plt
from tensorflow.keras import Model
from tensorflow.keras import Sequential
from tensorflow.keras.optimizers import Adam
from sklearn.preprocessing import StandardScaler
from tensorflow.keras.layers import Dense, Dropout
from sklearn.model_selection import train_test_split
from tensorflow.keras.losses import MeanSquaredLogarithmicError
from sklearn.preprocessing import OneHotEncoder

import numpy as np


from tensorflow.keras.layers import Dense, Dropout,LeakyReLU


TRAIN_DATA_PATH = '../data/test_train_split/training_split_deid_April_27_2022.csv'
TEST_DATA_PATH = '../data/test_train_split/test_split_deid_April_27_2022.csv'
TARGET_NAME = 'LT4'

In [30]:
print("Num GPUs Available: ", len(tf.config.list_physical_devices('GPU')))

Num GPUs Available:  2


In [3]:
# x_train = features, y_train = target
train_data = pd.read_csv(TRAIN_DATA_PATH)
test_data = pd.read_csv(TEST_DATA_PATH)

In [4]:
# function that does one hot encoding on categorical variables
def one_hot_encoder(x):
    ohe = OneHotEncoder()
    dat = x.to_numpy().reshape(len(x), 1)
    result = ohe.fit_transform(dat)
    return result.toarray()

In [5]:
tmp = one_hot_encoder(train_data['Gender'])
tmp = pd.DataFrame(tmp, columns=list(['Female', 'Male']))
train_data = pd.concat([train_data, tmp], axis=1)

tmp = one_hot_encoder(test_data['Gender'])
tmp = pd.DataFrame(tmp, columns=list(['Female', 'Male']))
test_data = pd.concat([test_data, tmp], axis=1)


In [6]:
tmp = one_hot_encoder(train_data['Calcium'])
tmp = pd.DataFrame(tmp, columns=list(['No_calcium', 'Takes_calcium']))
train_data = pd.concat([train_data, tmp], axis=1)

tmp = one_hot_encoder(test_data['Calcium'])
tmp = pd.DataFrame(tmp, columns=list(['No_calcium', 'Takes_calcium']))
test_data = pd.concat([test_data, tmp], axis=1)


In [7]:
tmp = one_hot_encoder(train_data['Calcitriol'])
tmp = pd.DataFrame(tmp, columns=list(['No_calcitriol', 'Takes_calcitriol']))
train_data = pd.concat([train_data, tmp], axis=1)

tmp = one_hot_encoder(test_data['Calcitriol'])
tmp = pd.DataFrame(tmp, columns=list(['No_calcitriol', 'Takes_calcitriol']))
test_data = pd.concat([test_data, tmp], axis=1)


In [8]:
train = train_data[['LT4', 'logTSH', 'Weight', 'Height', 'Female', 'Male', 'Age', 'Takes_calcium', 'No_calcium']]
test = test_data[['LT4', 'logTSH', 'Weight', 'Height', 'Female', 'Male', 'Age', 'Takes_calcium', 'No_calcium']]

In [9]:
test

LT4    logTSH  Weight  Height  Female  Male  Age  Takes_calcium  \
0    137.0 -1.832581   87.54  165.74     1.0   0.0   62            1.0   
1    137.0 -1.771957   86.64  170.18     1.0   0.0   37            1.0   
2    100.0 -0.673345   63.05  149.86     1.0   0.0   52            1.0   
3    200.0  0.615186  118.93  170.18     0.0   1.0   49            1.0   
4    150.0  1.342865   98.60  182.90     0.0   1.0   54            0.0   
..     ...       ...     ...     ...     ...   ...  ...            ...   
186  112.0  2.219203   71.49  160.02     1.0   0.0   33            1.0   
187  137.0 -2.207275   84.82  170.18     0.0   1.0   56            1.0   
188  200.0  0.231112  131.54  187.96     0.0   1.0   48            1.0   
189  224.0 -1.021651  119.30  164.50     1.0   0.0   24            1.0   
190  137.0 -2.813411   87.60  172.70     1.0   0.0   63            1.0   

     No_calcium  
0           0.0  
1           0.0  
2           0.0  
3           0.0  
4           1.0  
..          ...  
186         0.0  
187         0.0  
188         0.0  
189         0.0  
190         0.0  

[191 rows x 9 columns]

In [10]:
x_train, y_train = train.drop(TARGET_NAME, axis=1), train[TARGET_NAME]
x_test, y_test = test.drop(TARGET_NAME, axis=1), test[TARGET_NAME]

In [11]:
"""
  Standard Scale test and train data
  Z - Score normalization
"""
def scale_datasets(x_train, x_test):
    standard_scaler = StandardScaler()
  
    x_train_scaled = pd.DataFrame(
        standard_scaler.fit_transform(x_train),
        columns=x_train.columns
    )

    x_test_scaled = pd.DataFrame(
        standard_scaler.transform(x_test),
        columns = x_test.columns
    )
    return x_train_scaled, x_test_scaled

x_train_scaled, x_test_scaled = scale_datasets(x_train, x_test)

In [12]:
x_train_scaled

logTSH    Weight    Height    Female      Male       Age  \
0   -0.765689  2.036715  1.473469 -1.607517  1.607517  0.517391   
1    1.795543 -0.988363 -0.907885  0.622077 -0.622077  1.973196   
2    1.438981  0.980598  0.699605 -1.607517  1.607517 -0.739895   
3    0.976457 -0.898759  0.185046  0.622077 -0.622077  1.377640   
4   -0.222350 -1.072834 -0.136047  0.622077 -0.622077 -1.269278   
..        ...       ...       ...       ...       ...       ...   
762  0.775444  2.078717 -0.329513  0.622077 -0.622077  1.112948   
763 -0.920205 -0.621546 -0.586792  0.622077 -0.622077  0.914429   
764 -0.038152  1.329681 -0.458153  0.622077 -0.622077 -1.467797   
765 -0.055764 -1.104102 -0.846098  0.622077 -0.622077 -0.938413   
766  1.195108 -0.203392 -0.582741  0.622077 -0.622077  0.318872   

     Takes_calcium  No_calcium  
0         0.549734   -0.549734  
1         0.549734   -0.549734  
2        -1.819063    1.819063  
3         0.549734   -0.549734  
4         0.549734   -0.549734  
..             ...         ...  
762       0.549734   -0.549734  
763       0.549734   -0.549734  
764       0.549734   -0.549734  
765      -1.819063    1.819063  
766      -1.819063    1.819063  

[767 rows x 8 columns]

In [14]:
# defining fully connected NN model

hidden_units1 = 256
hidden_units2 = 512
hidden_units3 = 128
learning_rate = 0.0001
# Creating model using the Sequential in tensorflow
def build_model_using_sequential():
  model = Sequential([
    Dense(hidden_units1, kernel_initializer='normal', activation='relu'),
    Dropout(0.2),
    Dense(hidden_units2, kernel_initializer='normal', activation='relu'),
    Dropout(0.2),
    Dense(hidden_units3, kernel_initializer='normal', activation='relu'),
    Dense(1, kernel_initializer='normal', activation='linear')
  ])
  return model



In [15]:
accuracy_all = []
accuracy_normal = []
accuracy_exact = []


for i in range(10):
    
    # build the model
    model = build_model_using_sequential()
    
    # loss function
    msle = MeanSquaredLogarithmicError()
    # msle = MeanSquaredError()
    model.compile(
        loss=msle, 
        optimizer=Adam(learning_rate=learning_rate), 
        metrics=[msle]
    )
    # train the model
    history = model.fit(
        x_train_scaled.values, 
        y_train.values, 
        epochs=2000, 
        batch_size=64,
        validation_split=0
    )
    
    
    x_test['prediction'] = model.predict(x_test_scaled)
    x_test['LT4'] = y_test
    x_test['diff'] = abs(x_test['LT4'] - x_test['prediction'])
    
    # calculate and printaccuracy_all accuracies
    print("Run " + str(i) + " all TSH: " + str(sum(abs(x_test['LT4'] - x_test['prediction']) <= 12.5)/x_test.shape[0]))
    accuracy_all.append(sum(abs(x_test['LT4'] - x_test['prediction']) <= 12.5)/x_test.shape[0])
    x_test['TSH'] = np.exp(x_test['logTSH'])
    x_test_normal = x_test[x_test['TSH'] > 0.45]
    x_test_normal = x_test_normal[x_test_normal['TSH'] < 5]
    print("Run " + str(i) + " normal TSH: " + str(sum(abs(x_test_normal['LT4'] - x_test_normal['prediction']) <= 12.5)/x_test_normal.shape[0]))
    accuracy_normal.append(sum(abs(x_test_normal['LT4'] - x_test_normal['prediction']) <= 12.5)/x_test_normal.shape[0])
    
    
    # this calculates accuracy of predicting exact rounded dose
    LT_doses = [75, 88 ,100, 112, 125, 137, 150, 175, 200, 224, 250]

    # function rounds to a nearest dose in a list
    def closest_value(input_list, input_value): 
      arr = np.asarray(input_list)
      i = (np.abs(arr - input_value)).argmin()
      return arr[i]

    rounded_LT4 = x_test['LT4'].to_list()
    x_test['LT4_rounded'] = [closest_value(LT_doses, x) for x in rounded_LT4]

    predicted_rounded_LT4 = x_test['prediction'].to_list()
    x_test['predicted_LT4_rounded'] = [closest_value(LT_doses, x) for x in predicted_rounded_LT4]

    print("Run " + str(i) + " exact LT4 dose: ", sum(x_test['LT4_rounded'] == x_test['predicted_LT4_rounded'])/x_test.shape[0])

    accuracy_exact.append(sum(x_test['LT4_rounded'] == x_test['predicted_LT4_rounded'])/x_test.shape[0])
    

Epoch 1/2000


2022-04-30 19:37:06.474817: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2022-04-30 19:37:06.659299: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:936] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-04-30 19:37:06.659542: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:936] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-04-30 19:37:06.659756: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:936] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zer

12/12 [==============================] - 1s 2ms/step - loss: 23.7684 - mean_squared_logarithmic_error: 23.7668
Epoch 2/2000
12/12 [==============================] - 0s 2ms/step - loss: 22.5688 - mean_squared_logarithmic_error: 22.5681
Epoch 3/2000
12/12 [==============================] - 0s 2ms/step - loss: 21.3079 - mean_squared_logarithmic_error: 21.3077
Epoch 4/2000
12/12 [==============================] - 0s 2ms/step - loss: 19.8999 - mean_squared_logarithmic_error: 19.8992
Epoch 5/2000
12/12 [==============================] - 0s 2ms/step - loss: 18.3355 - mean_squared_logarithmic_error: 18.3339
Epoch 6/2000
12/12 [==============================] - 0s 2ms/step - loss: 16.6597 - mean_squared_logarithmic_error: 16.6582
Epoch 7/2000
12/12 [==============================] - 0s 2ms/step - loss: 14.9651 - mean_squared_logarithmic_error: 14.9642
Epoch 8/2000
12/12 [==============================] - 0s 2ms/step - loss: 13.3451 - mean_squared_logarithmic_error: 13.3436
Epoch 9/2000
12/12 [=

12/12 [==============================] - 0s 2ms/step - loss: 0.0298 - mean_squared_logarithmic_error: 0.0298
Epoch 134/2000
12/12 [==============================] - 0s 1ms/step - loss: 0.0306 - mean_squared_logarithmic_error: 0.0306
Epoch 135/2000
12/12 [==============================] - 0s 1ms/step - loss: 0.0303 - mean_squared_logarithmic_error: 0.0304
Epoch 136/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0278 - mean_squared_logarithmic_error: 0.0278
Epoch 137/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0281 - mean_squared_logarithmic_error: 0.0281
Epoch 138/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0283 - mean_squared_logarithmic_error: 0.0283
Epoch 139/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0280 - mean_squared_logarithmic_error: 0.0280
Epoch 140/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0291 - mean_squared_logarithmic_error: 0.0291
Epoch 141/2000
12/12 [=

12/12 [==============================] - 0s 2ms/step - loss: 0.0197 - mean_squared_logarithmic_error: 0.0197
Epoch 266/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0172 - mean_squared_logarithmic_error: 0.0172
Epoch 267/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0183 - mean_squared_logarithmic_error: 0.0183
Epoch 268/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0186 - mean_squared_logarithmic_error: 0.0186
Epoch 269/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0181 - mean_squared_logarithmic_error: 0.0181
Epoch 270/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0183 - mean_squared_logarithmic_error: 0.0183
Epoch 271/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0179 - mean_squared_logarithmic_error: 0.0179
Epoch 272/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0175 - mean_squared_logarithmic_error: 0.0175
Epoch 273/2000
12/12 [=

...

12/12 [==============================] - 0s 2ms/step - loss: 0.0115 - mean_squared_logarithmic_error: 0.0115
Epoch 1385/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0109 - mean_squared_logarithmic_error: 0.0109
Epoch 1386/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0114 - mean_squared_logarithmic_error: 0.0114
Epoch 1387/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0105 - mean_squared_logarithmic_error: 0.0105
Epoch 1388/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0108 - mean_squared_logarithmic_error: 0.0108
Epoch 1389/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0118 - mean_squared_logarithmic_error: 0.0118
Epoch 1390/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0110 - mean_squared_logarithmic_error: 0.0110
Epoch 1391/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0108 - mean_squared_logarithmic_error: 0.0108
Epoch 1392/2000


12/12 [==============================] - 0s 2ms/step - loss: 0.0111 - mean_squared_logarithmic_error: 0.0111
Epoch 1515/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0116 - mean_squared_logarithmic_error: 0.0116
Epoch 1516/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0110 - mean_squared_logarithmic_error: 0.0110
Epoch 1517/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0111 - mean_squared_logarithmic_error: 0.0111
Epoch 1518/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0115 - mean_squared_logarithmic_error: 0.0115
Epoch 1519/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0110 - mean_squared_logarithmic_error: 0.0110
Epoch 1520/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0110 - mean_squared_logarithmic_error: 0.0110
Epoch 1521/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0113 - mean_squared_logarithmic_error: 0.0113
Epoch 1522/2000


12/12 [==============================] - 0s 2ms/step - loss: 0.0114 - mean_squared_logarithmic_error: 0.0114
Epoch 1645/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0111 - mean_squared_logarithmic_error: 0.0111
Epoch 1646/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0115 - mean_squared_logarithmic_error: 0.0115
Epoch 1647/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0110 - mean_squared_logarithmic_error: 0.0110
Epoch 1648/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0110 - mean_squared_logarithmic_error: 0.0110
Epoch 1649/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0112 - mean_squared_logarithmic_error: 0.0112
Epoch 1650/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0116 - mean_squared_logarithmic_error: 0.0116
Epoch 1651/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0111 - mean_squared_logarithmic_error: 0.0111
Epoch 1652/2000


12/12 [==============================] - 0s 2ms/step - loss: 0.0114 - mean_squared_logarithmic_error: 0.0114
Epoch 1775/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0109 - mean_squared_logarithmic_error: 0.0109
Epoch 1776/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0114 - mean_squared_logarithmic_error: 0.0114
Epoch 1777/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0103 - mean_squared_logarithmic_error: 0.0103
Epoch 1778/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0112 - mean_squared_logarithmic_error: 0.0112
Epoch 1779/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0108 - mean_squared_logarithmic_error: 0.0108
Epoch 1780/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0111 - mean_squared_logarithmic_error: 0.0111
Epoch 1781/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0110 - mean_squared_logarithmic_error: 0.0110
Epoch 1782/2000


12/12 [==============================] - 0s 2ms/step - loss: 0.0106 - mean_squared_logarithmic_error: 0.0106
Epoch 1905/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0110 - mean_squared_logarithmic_error: 0.0110
Epoch 1906/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0106 - mean_squared_logarithmic_error: 0.0106
Epoch 1907/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0109 - mean_squared_logarithmic_error: 0.0109
Epoch 1908/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0108 - mean_squared_logarithmic_error: 0.0108
Epoch 1909/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0104 - mean_squared_logarithmic_error: 0.0104
Epoch 1910/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0114 - mean_squared_logarithmic_error: 0.0114
Epoch 1911/2000
12/12 [==============================] - 0s 2ms/step - loss: 0.0111 - mean_squared_logarithmic_error: 0.0111
Epoch 1912/2000


In [16]:
print("Average accuracy on test data set: ", np.mean(accuracy_all))
print("Average accuracy on test data set, normal TSH: ", np.mean(accuracy_normal))
print("Average accuracy of predicting exact LT4 dose: ", np.mean(accuracy_exact))



Average accuracy on test data set:  0.6230366492146598
Average accuracy on test data set, normal TSH:  0.661764705882353
Average accuracy of predictin exact LT4 dose:  0.42094240837696334


In [23]:
linearlinearLT_doses = [75, 88 ,100, 112, 125, 137, 150, 175, 200, 224, 250]

# this calculates accuracy of predicting exact rounded dose

# function rounds to a nearest dose in a list
def closest_value(input_list, input_value): 
  arr = np.asarray(input_list)
  i = (np.abs(arr - input_value)).argmin()
  return arr[i]

rounded_LT4 = x_test['LT4'].to_list()
x_test['LT4_rounded'] = [closest_value(LT_doses, x) for x in rounded_LT4]

predicted_rounded_LT4 = x_test['prediction'].to_list()
x_test['predicted_LT4_rounded'] = [closest_value(LT_doses, x) for x in predicted_rounded_LT4]

print(sum(x_test['LT4_rounded'] == x_test['predicted_LT4_rounded'])/x_test.shape[0])

x_test.to_csv('../Results/NN_regression_inference_on test_April25_2022.csv')

0.40522875816993464


In [21]:
# CROSS-VALIDATION

#deleting previous run
if 'val_folds' in locals() or 'val_folds' in globals():
    del(val_folds)
    
accuracy_all = []
accuracy_normal = []

from sklearn.model_selection import cross_val_score,KFold
kf = KFold(n_splits=5, shuffle = True)

for train_index, test_index in kf.split(train):

    train_cv = train.iloc[train_index]
    test_cv = train.iloc[test_index]
    
    x_train, y_train = train_cv.drop(TARGET_NAME, axis=1), train_cv[TARGET_NAME]
    x_test, y_test = test_cv.drop(TARGET_NAME, axis=1), test_cv[TARGET_NAME]
    
    x_train_scaled, x_test_scaled = scale_datasets(x_train, x_test)
    
    # build the model
    model = build_model_using_sequential()
    
    # loss function
    msle = MeanSquaredLogarithmicError()
    # msle = MeanSquaredError()
    model.compile(
        loss=msle, 
        optimizer=Adam(learning_rate=learning_rate), 
        metrics=[msle]
    )
    # train the model
    history = model.fit(
        x_train_scaled.values, 
        y_train.values, 
        epochs=2000, 
        batch_size=32,
        validation_split=0
    )
    
    x_test['prediction'] = model.predict(x_test_scaled)
    x_test['LT4'] = y_test
    x_test['diff'] = abs(x_test['LT4'] - x_test['prediction'])
    
    if 'val_folds' in locals() or 'val_folds' in globals():
        val_folds = pd.concat([val_folds, x_test], axis = 0)
    else:
        val_folds = x_test
    
    # calculate and print accuracies
    print("Run " + str(i) + " all TSH: " + str(sum(abs(x_test['LT4'] - x_test['prediction']) <= 12.5)/x_test.shape[0]))
    accuracy_all.append(sum(abs(x_test['LT4'] - x_test['prediction']) <= 12.5)/x_test.shape[0])
    x_test['TSH'] = np.exp(x_test['logTSH'])
    x_test_normal = x_test[x_test['TSH'] > 0.45]
    x_test_normal = x_test_normal[x_test_normal['TSH'] < 4.5]
    print("Run " + str(i) + " normal TSH: " + str(sum(abs(x_test_normal['LT4'] - x_test_normal['prediction']) <= 12.5)/x_test_normal.shape[0]))
    accuracy_normal.append(sum(abs(x_test_normal['LT4'] - x_test_normal['prediction']) <= 12.5)/x_test_normal.shape[0])
    


Epoch 1/2000
20/20 [==============================] - 0s 2ms/step - loss: 24.1708 - mean_squared_logarithmic_error: 24.1820
Epoch 2/2000
20/20 [==============================] - 0s 2ms/step - loss: 22.7080 - mean_squared_logarithmic_error: 22.6991
Epoch 3/2000
20/20 [==============================] - 0s 2ms/step - loss: 20.7016 - mean_squared_logarithmic_error: 20.6414
Epoch 4/2000
20/20 [==============================] - 0s 2ms/step - loss: 18.2348 - mean_squared_logarithmic_error: 18.1965
Epoch 5/2000
20/20 [==============================] - 0s 2ms/step - loss: 15.5165 - mean_squared_logarithmic_error: 15.4800
Epoch 6/2000
20/20 [==============================] - 0s 2ms/step - loss: 12.9285 - mean_squared_logarithmic_error: 12.9388
Epoch 7/2000
20/20 [==============================] - 0s 2ms/step - loss: 10.7357 - mean_squared_logarithmic_error: 10.6449
Epoch 8/2000
20/20 [==============================] - 0s 2ms/step - loss: 8.9319 - mean_squared_logarithmic_error: 8.9400
Epoch 9/20

20/20 [==============================] - 0s 2ms/step - loss: 0.0198 - mean_squared_logarithmic_error: 0.0196
Epoch 134/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0203 - mean_squared_logarithmic_error: 0.0202
Epoch 135/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0210 - mean_squared_logarithmic_error: 0.0210
Epoch 136/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0208 - mean_squared_logarithmic_error: 0.0211
Epoch 137/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0196 - mean_squared_logarithmic_error: 0.0189
Epoch 138/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0202 - mean_squared_logarithmic_error: 0.0198
Epoch 139/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0193 - mean_squared_logarithmic_error: 0.0196
Epoch 140/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0197 - mean_squared_logarithmic_error: 0.0192
Epoch 141/2000
20/20 [=

20/20 [==============================] - 0s 2ms/step - loss: 0.0150 - mean_squared_logarithmic_error: 0.0148
Epoch 266/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0146 - mean_squared_logarithmic_error: 0.0143
Epoch 267/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0148 - mean_squared_logarithmic_error: 0.0152
Epoch 268/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0141 - mean_squared_logarithmic_error: 0.0141
Epoch 269/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0149 - mean_squared_logarithmic_error: 0.0147
Epoch 270/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0142 - mean_squared_logarithmic_error: 0.0137
Epoch 271/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0141 - mean_squared_logarithmic_error: 0.0142
Epoch 272/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0144 - mean_squared_logarithmic_error: 0.0144
Epoch 273/2000
20/20 [=

20/20 [==============================] - 0s 2ms/step - loss: 0.0130 - mean_squared_logarithmic_error: 0.0128
Epoch 398/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0133 - mean_squared_logarithmic_error: 0.0140
Epoch 399/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0134 - mean_squared_logarithmic_error: 0.0140
Epoch 400/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0129 - mean_squared_logarithmic_error: 0.0125
Epoch 401/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0123 - mean_squared_logarithmic_error: 0.0121
Epoch 402/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0115 - mean_squared_logarithmic_error: 0.0115
Epoch 403/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0120 - mean_squared_logarithmic_error: 0.0118
Epoch 404/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0123 - mean_squared_logarithmic_error: 0.0120
Epoch 405/2000
20/20 [=

20/20 [==============================] - 0s 2ms/step - loss: 0.0119 - mean_squared_logarithmic_error: 0.0129
Epoch 530/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0119 - mean_squared_logarithmic_error: 0.0125
Epoch 531/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0125 - mean_squared_logarithmic_error: 0.0126
Epoch 532/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0122 - mean_squared_logarithmic_error: 0.0120
Epoch 533/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0121 - mean_squared_logarithmic_error: 0.0131
Epoch 534/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0124 - mean_squared_logarithmic_error: 0.0133
Epoch 535/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0122 - mean_squared_logarithmic_error: 0.0118
Epoch 536/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0130 - mean_squared_logarithmic_error: 0.0129
Epoch 537/2000
20/20 [=

...

20/20 [==============================] - 0s 2ms/step - loss: 0.0103 - mean_squared_logarithmic_error: 0.0103
Epoch 1372/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0100 - mean_squared_logarithmic_error: 0.0098
Epoch 1373/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0105 - mean_squared_logarithmic_error: 0.0103
Epoch 1374/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0099 - mean_squared_logarithmic_error: 0.0097
Epoch 1375/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0102 - mean_squared_logarithmic_error: 0.0106
Epoch 1376/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0107 - mean_squared_logarithmic_error: 0.0104
Epoch 1377/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0103 - mean_squared_logarithmic_error: 0.0103
Epoch 1378/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0108 - mean_squared_logarithmic_error: 0.0108
Epoch 1379/2000


20/20 [==============================] - 0s 2ms/step - loss: 0.0101 - mean_squared_logarithmic_error: 0.0098
Epoch 1502/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0101 - mean_squared_logarithmic_error: 0.0103
Epoch 1503/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0105 - mean_squared_logarithmic_error: 0.0105
Epoch 1504/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0104 - mean_squared_logarithmic_error: 0.0102
Epoch 1505/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0105 - mean_squared_logarithmic_error: 0.0108
Epoch 1506/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0100 - mean_squared_logarithmic_error: 0.0099
Epoch 1507/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0105 - mean_squared_logarithmic_error: 0.0105
Epoch 1508/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0109 - mean_squared_logarithmic_error: 0.0110
Epoch 1509/2000


20/20 [==============================] - 0s 2ms/step - loss: 0.0099 - mean_squared_logarithmic_error: 0.0101
Epoch 1632/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0105 - mean_squared_logarithmic_error: 0.0111
Epoch 1633/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0102 - mean_squared_logarithmic_error: 0.0105
Epoch 1634/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0100 - mean_squared_logarithmic_error: 0.0099
Epoch 1635/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0105 - mean_squared_logarithmic_error: 0.0103
Epoch 1636/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0100 - mean_squared_logarithmic_error: 0.0098
Epoch 1637/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0106 - mean_squared_logarithmic_error: 0.0104
Epoch 1638/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0103 - mean_squared_logarithmic_error: 0.0101
Epoch 1639/2000


20/20 [==============================] - 0s 1ms/step - loss: 0.0105 - mean_squared_logarithmic_error: 0.0105
Epoch 1762/2000
20/20 [==============================] - 0s 1ms/step - loss: 0.0095 - mean_squared_logarithmic_error: 0.0094
Epoch 1763/2000
20/20 [==============================] - 0s 1ms/step - loss: 0.0096 - mean_squared_logarithmic_error: 0.0094
Epoch 1764/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0100 - mean_squared_logarithmic_error: 0.0098
Epoch 1765/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0102 - mean_squared_logarithmic_error: 0.0103
Epoch 1766/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0096 - mean_squared_logarithmic_error: 0.0094
Epoch 1767/2000
20/20 [==============================] - 0s 1ms/step - loss: 0.0104 - mean_squared_logarithmic_error: 0.0106
Epoch 1768/2000
20/20 [==============================] - 0s 1ms/step - loss: 0.0102 - mean_squared_logarithmic_error: 0.0105
Epoch 1769/2000


20/20 [==============================] - 0s 1ms/step - loss: 0.0097 - mean_squared_logarithmic_error: 0.0095
Epoch 1892/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0098 - mean_squared_logarithmic_error: 0.0097
Epoch 1893/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0100 - mean_squared_logarithmic_error: 0.0101
Epoch 1894/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0100 - mean_squared_logarithmic_error: 0.0100
Epoch 1895/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0095 - mean_squared_logarithmic_error: 0.0093
Epoch 1896/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0095 - mean_squared_logarithmic_error: 0.0094
Epoch 1897/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0100 - mean_squared_logarithmic_error: 0.0102
Epoch 1898/2000
20/20 [==============================] - 0s 2ms/step - loss: 0.0094 - mean_squared_logarithmic_error: 0.0095
Epoch 1899/2000


In [29]:
print("Average accuracy on test data set: ", np.mean(accuracy_all))
print("Average accuracy on test data set, normal TSH: ", np.mean(accuracy_normal))

rounded_LT4 = val_folds['LT4'].to_list()
val_folds['LT4_rounded'] = [closest_value(LT_doses, x) for x in rounded_LT4]

predicted_rounded_LT4 = val_folds['prediction'].to_list()
val_folds['predicted_LT4_rounded'] = [closest_value(LT_doses, x) for x in predicted_rounded_LT4]

print("Average accuracy of predicting exact LT4 dose: ", 
      sum(val_folds['LT4_rounded'] == val_folds['predicted_LT4_rounded'])/val_folds.shape[0])


Average accuracy on test data set:  0.6180290297937356
Average accuracy on test data set, normal TSH:  0.6524035751186262
Average accuracy of predicting exact LT4 dose:  0.41199478487614083
